In [1]:
import numpy as np
import pandas as pd
from itertools import product
import tensorflow as tf
from time import time
import multiprocessing
from sklearn.metrics import r2_score
from sklearn.preprocessing import MinMaxScaler, StandardScaler
from sklearn.model_selection import train_test_split
from keras.models import Model
from keras.layers import Input, Dense, Concatenate, Lambda, Dropout
from keras.optimizers import Adam
from keras.regularizers import l2
from sklearn.metrics import mean_absolute_error, mean_absolute_percentage_error
from sklearn.metrics import mean_squared_error, r2_score
from keras.callbacks import ModelCheckpoint, ReduceLROnPlateau, EarlyStopping
import matplotlib.pyplot as plt
import os

2025-02-05 13:49:36.809724: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-02-05 13:49:36.822589: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1738781376.836144  788238 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1738781376.840229  788238 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-02-05 13:49:36.854971: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [2]:
# Set environment variables before TensorFlow initializes
os.environ["CUDA_VISIBLE_DEVICES"] = "1"  # Restrict TensorFlow to only use GPU 1
os.environ["TF_ENABLE_ONEDNN_OPTS"] = "0"  # Disable oneDNN optimizations

# Ensure TensorFlow only sees GPU 1
gpus = tf.config.list_physical_devices('GPU')

if gpus:
    try:
        # Enable memory growth for GPU 1
        tf.config.experimental.set_memory_growth(gpus[0], True)  # gpus[0] now refers to GPU 1
        print(f"Using only GPU 1 (CUDA_VISIBLE_DEVICES=1).")
    except RuntimeError as e:
        print(f"Error setting memory growth: {e}")
else:
    print("No GPUs found! Check CUDA_VISIBLE_DEVICES setting.")

# Print number of GPUs available (should only be 1 after restriction)
print("Num GPUs Available:", len(gpus))

Using only GPU 1 (CUDA_VISIBLE_DEVICES=1).
Num GPUs Available: 1


In [ ]:
df = pd.read_csv("Complete_BF_CPP_XY_Data.csv")
df = df.sample(frac=1, random_state=42).reset_index(drop=True)
X = df.iloc[:, 1:5]
Y = df.iloc[:, 5:27]
X_scaler = StandardScaler()
X_scaled = X_scaler.fit_transform(X)
Y_scaler = StandardScaler()
Y_scaled = Y_scaler.fit_transform(Y)
X_train, X_test, Y_train, Y_test = train_test_split(X_scaled, Y_scaled, test_size=0.2, random_state=1)

/tmp/ipykernel_788238/2789577395.py:1: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("Complete_BF_CPP_XY_Data.csv")


In [4]:
def create_model(layer1_neurons, learning_rate): # , l2_lambda=0.01, dropout_rate=0.5
    # Input layer
    input_layer = Input(shape=(4,), name="Input_Layer")
    
    # First network (Network 1) with L2 regularization and dropout
    x = Dense(layer1_neurons[0], activation='relu', name="Dense_Layer_1")(input_layer) # , kernel_regularizer=l2(l2_lambda)
    #x = Dropout(dropout_rate)(x)  # Apply dropout after each dense layer
    
    for i, neurons in enumerate(layer1_neurons[1:], start=2):
        x = Dense(neurons, activation='relu', name=f"Dense_Layer_{i}")(x) # , kernel_regularizer=l2(l2_lambda)
        #x = Dropout(dropout_rate)(x)  # Apply dropout

    # Output layer
    output_1 = Dense(22, activation='linear', name="Output_Layer_2")(x)
    
    # Define the model with the specified input and output
    model = Model(inputs=input_layer, outputs=output_1, name="Model_2")
    
    # Compile the model
    optimizer = Adam(learning_rate=learning_rate)
    model.compile(optimizer=optimizer, loss='mse')
    
    return model

In [5]:
# Create the model with L2 regularization and dropout
model = create_model([600, 600, 600, 600, 600, 600, 600], 1e-3) # , l2_lambda=1e-5, dropout_rate=0.1
model.summary()

I0000 00:00:1738781379.082135  788238 gpu_device.cc:2022] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 46672 MB memory:  -> device: 0, name: NVIDIA RTX 6000 Ada Generation, pci bus id: 0000:21:00.0, compute capability: 8.9


Model: "Model_2"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ Input_Layer (InputLayer)        │ (None, 4)              │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ Dense_Layer_1 (Dense)           │ (None, 600)            │         3,000 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ Dense_Layer_2 (Dense)           │ (None, 600)            │       360,600 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ Dense_Layer_3 (Dense)           │ (None, 600)            │       360,600 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ Dense_Layer_4 (Dense)           │ (None, 600)            │       360,600 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ Dense_Layer_5 (Dense)           │ (None, 600)            │       360,600 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ Dense_Layer_6 (Dense)           │ (None, 600)            │       360,600 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ Dense_Layer_7 (Dense)           │ (None, 600)            │       360,600 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ Output_Layer_2 (Dense)          │ (None, 22)             │        13,222 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 2,179,822 (8.32 MB)

 Trainable params: 2,179,822 (8.32 MB)

 Non-trainable params: 0 (0.00 B)

In [ ]:
reduce_lr = ReduceLROnPlateau(monitor='val_loss', factor=0.92, patience=25, min_lr=0, verbose=1, mode='min')
early_stopping = EarlyStopping(monitor='val_loss', patience=200, restore_best_weights=True, verbose=1, mode='min')
checkpoint = ModelCheckpoint('best_ConcNNFP_std_1000_64.keras', monitor='val_loss', save_best_only=True, mode='min', verbose=1)
history = model.fit(
        X_train,
        Y_train,  # Do this both for MinMax Scaled Y and Standard Scaled Y. Do not touch to X.
        epochs=2000,
        batch_size=256,
        validation_split=0.15,
        verbose=1,
        callbacks=[reduce_lr, early_stopping, checkpoint]
    )

Epoch 1/1000


I0000 00:00:1738781382.242181  791535 service.cc:148] XLA service 0x2b39bde0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
I0000 00:00:1738781382.242270  791535 service.cc:156]   StreamExecutor device (0): NVIDIA RTX 6000 Ada Generation, Compute Capability 8.9
2025-02-05 13:49:42.302926: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:268] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.


I0000 00:00:1738781382.670012  791535 cuda_dnn.cc:529] Loaded cuDNN version 90300


2025-02-05 13:49:43.816300: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_506', 8 bytes spill stores, 8 bytes spill loads



2025-02-05 13:49:44.123933: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_299', 32 bytes spill stores, 32 bytes spill loads

2025-02-05 13:49:44.159250: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_299', 164 bytes spill stores, 164 bytes spill loads

2025-02-05 13:49:44.177313: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_383', 116 bytes spill stores, 116 bytes spill loads

2025-02-05 13:49:44.185963: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_299', 36 bytes spill stores, 36 bytes spill loads

2025-02-05 13:49:44.221391: I external/local_xla/xla/stream_

...


326/367 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - loss: 0.1125


365/367 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - loss: 0.1154


Epoch 1000: val_loss did not improve from 0.23288



367/367 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 0.1156 - val_loss: 0.2391 - learning_rate: 1.2436e-04


Restoring model weights from the end of the best epoch: 954.


In [7]:
Y_pred = model.predict(X_test, verbose=0)
Y_train_pred = model.predict(X_train, verbose=0)

y_pred = Y_scaler.inverse_transform(Y_pred)
y_test = Y_scaler.inverse_transform(Y_test)

y_train_pred = Y_scaler.inverse_transform(Y_train_pred)
y_train = Y_scaler.inverse_transform(Y_train)

2025-02-05 14:02:03.953839: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_68', 196 bytes spill stores, 196 bytes spill loads

2025-02-05 14:02:03.998352: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_26', 436 bytes spill stores, 476 bytes spill loads

2025-02-05 14:02:04.010070: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_26', 36 bytes spill stores, 36 bytes spill loads

2025-02-05 14:02:04.013029: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_68', 116 bytes spill stores, 116 bytes spill loads

2025-02-05 14:02:04.016381: I external/local_xla/xla/stream_ex

2025-02-05 14:02:05.246495: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_26', 244 bytes spill stores, 268 bytes spill loads

2025-02-05 14:02:05.252880: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_26', 36 bytes spill stores, 36 bytes spill loads

2025-02-05 14:02:05.318913: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_68', 196 bytes spill stores, 196 bytes spill loads



2025-02-05 14:02:07.105949: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_26', 64 bytes spill stores, 64 bytes spill loads

2025-02-05 14:02:07.118171: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_68', 116 bytes spill stores, 116 bytes spill loads

2025-02-05 14:02:07.132011: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_26', 412 bytes spill stores, 404 bytes spill loads

2025-02-05 14:02:07.153352: I external/local_xla/xla/stream_executor/cuda/cuda_asm_compiler.cc:397] ptxas warning : Registers are spilled to local memory in function 'gemm_fusion_dot_68', 196 bytes spill stores, 196 bytes spill loads

2025-02-05 14:02:07.187390: I external/local_xla/xla/stream_ex

In [8]:
mae_y_test = mean_absolute_error(y_test, y_pred)
mape_y_test = np.mean(np.abs((y_test - y_pred) / y_pred)) * 100
mse_y_test = mean_squared_error(y_test, y_pred)
rmse_y_test = np.sqrt(mse_y_test)
r2_y_test = r2_score(y_test, y_pred)

mae_y_train = mean_absolute_error(y_train, y_train_pred)
mape_y_train = np.mean(np.abs((y_train - y_train_pred) / y_train)) * 100
mse_y_train = mean_squared_error(y_train, y_train_pred)
rmse_y_train = np.sqrt(mse_y_train)
r2_y_train = r2_score(y_train, y_train_pred)

print("\nEvaluation metrics for Y2 (training):")
print(f"MAE (Y2 train): {mae_y_train}")
print(f"MAPE (Y2 train): {mape_y_train}%")
print(f"MSE (Y2 train): {mse_y_train}")
print(f"RMSE (Y2 train): {rmse_y_train}")
print(f"R² (Y2 train): {r2_y_train}")

print("\nEvaluation metrics for Y2 (test):")
print(f"MAE (Y2 test): {mae_y_test}")
print(f"MAPE (Y2 test): {mape_y_test}%")
print(f"MSE (Y2 test): {mse_y_test}")
print(f"RMSE (Y2 test): {rmse_y_test}")
print(f"R² (Y2 test): {r2_y_test}")


Evaluation metrics for Y2 (training):
MAE (Y2 train): 31.933530208569334
MSE (Y2 train): 60831.79333026055
RMSE (Y2 train): 246.64102118313684
R² (Y2 train): 0.8507820549532462

Evaluation metrics for Y2 (test):
MAE (Y2 test): 38.22587809902158
MSE (Y2 test): 90088.38309794346
RMSE (Y2 test): 300.14726901630047
R² (Y2 test): 0.775256394249378
